### Connecting to the postgis using sqlalchemy and manipulating the tables as geodataframes

## functions

In [1]:
def count_features(gdf, seamark):
    '''Count how many rows have that specific seamark type inside'''

    counter = 0

    #iterate through each row of the df 
    for index, row in gdf.iterrows():

        #iterate through each item and key of the dictionary inside the tags column
        for key, value in row['tags'].items():
            if key == 'seamark:type' and value == seamark:
                counter += 1
            else:
                pass

    print(counter)

In [2]:
def filtered_gdf_seamark(gdf, seamark):
    '''Create new gdf with only the rows with the specified seamark'''

    return gdf[gdf['tags'].apply(lambda x: seamark in x.values())]

In [3]:
# Define a function to format the lengthy dict column
def format_dict(d):
    # Split the dict into several lines
    lines = [f"{k}: {v}" for k, v in d.items()]
    return "<br />".join(lines)

In [100]:
table_list_gdf_nodes2['tags']

0                                                         {}
1                                                         {}
2                                                         {}
3                                                         {}
4          {'name': 'USCGC Cheyenne', 'image': 'https://w...
                                 ...                        
2098804                                                   {}
2098805                                                   {}
2098806                                                   {}
2098807                                                   {}
2098808                                                   {}
Name: tags, Length: 2098809, dtype: object

## public.nodes

In [175]:
import os
import sqlalchemy as db
import pandas as pd
import geopandas as gpd
from dotenv import load_dotenv

# Load the environment variables from the .env file
load_dotenv("./python_docker/.env")


# Connect to the PostgreSQL database using SQLAlchemy
engine = db.create_engine('postgresql://{user}:{pw}@{host}/{db}'
                           .format(user=os.environ.get("POSTGIS_USER"),
                                   pw=os.environ.get("POSTGIS_PASSWORD"),
                                   host="172.18.0.3",
                                   db=os.environ.get("POSTGIS_DATABASE"),
                                   port='5434'))

# # Connect to the PostgreSQL database using SQLAlchemy
# engine = db.create_engine('postgresql://{user}:{pw}@{host}/{db}'
#                            .format(user="myuser",
#                                    pw="mypassword",
#                                    host="172.18.0.2",
#                                    db="mydatabase",
#                                    port="5434"))


connection = engine.connect()

# Define SQL query to retrieve list of tables
#sql_query = "SELECT table_name FROM information_schema.tables WHERE table_schema = 'public'"

# query = "SELECT * FROM nodes LIMIT 500"
query = "SELECT * FROM nodes"

# Use pandas to read the SQL query into a dataframe
#table_list_df = pd.read_sql(sql_query, engine)

# Use geopandas to read the SQL query into a dataframe from postgis
table_list_gdf_nodes = gpd.read_postgis(query, engine)

# read timestamp type data as string
table_list_gdf_nodes['tstamp']=table_list_gdf_nodes['tstamp'].dt.strftime('%Y-%m-%d %H:%M:%S')

table_list_gdf_nodes.head(100)

id  version   user_id               tstamp  changeset_id   
0   7794434396        1  11392834  2020-08-07 12:17:42      89092064  \
1   7794434397        2  11392834  2023-04-02 13:03:10     134413348   
2   7794434398        1  11392834  2020-08-07 12:17:42      89092064   
3   7794434399        1  11392834  2020-08-07 12:17:42      89092064   
4   7794434429        4  11392834  2023-04-02 13:03:10     134413348   
..         ...      ...       ...                  ...           ...   
95  7796585756        1  11392834  2020-08-08 12:16:06      89126347   
96  7796585763        1  11392834  2020-08-08 12:16:06      89126347   
97  7796585764        1  11392834  2020-08-08 12:16:06      89126347   
98  7796605586        1  11392834  2020-08-08 12:46:01      89127137   
99  7796607473        1   2831457  2020-08-08 12:45:19      89127114   

                                                 tags   
0                                                  {}  \
1                                                  {}   
2                                                  {}   
3                                                  {}   
4   {'name': 'USCGC Cheyenne', 'image': 'https://w...   
..                                                ...   
95                                                 {}   
96                                                 {}   
97                                                 {}   
98                                                 {}   
99                                                 {}   

                          geom  
0   POINT (-90.20770 38.58973)  
1   POINT (-90.20780 38.58966)  
2   POINT (-90.20787 38.58970)  
3   POINT (-90.20915 38.58901)  
4   POINT (-90.20920 38.58715)  
..                         ...  
95  POINT (-95.96015 41.35094)  
96  POINT (-95.95910 41.35090)  
97  POINT (-95.95906 41.35085)  
98  POINT (-95.95844 41.35262)  
99    POINT (6.74731 52.66226)  

[100 rows x 7 columns]

In [176]:
# Create a copy of the df to test the functions
table_list_gdf_nodes2 = table_list_gdf_nodes.copy()

In [180]:
table_list_gdf_nodes2.head()

id  version   user_id               tstamp  changeset_id   
0  7794434396        1  11392834  2020-08-07 12:17:42      89092064  \
1  7794434397        2  11392834  2023-04-02 13:03:10     134413348   
2  7794434398        1  11392834  2020-08-07 12:17:42      89092064   
3  7794434399        1  11392834  2020-08-07 12:17:42      89092064   
4  7794434429        4  11392834  2023-04-02 13:03:10     134413348   

                                                tags   
0                                                 {}  \
1                                                 {}   
2                                                 {}   
3                                                 {}   
4  {'name': 'USCGC Cheyenne', 'image': 'https://w...   

                         geom  
0  POINT (-90.20770 38.58973)  
1  POINT (-90.20780 38.58966)  
2  POINT (-90.20787 38.58970)  
3  POINT (-90.20915 38.58901)  
4  POINT (-90.20920 38.58715)

In [20]:
count_features(table_list_gdf_nodes2, 'buoy_lateral')

56801


In [21]:
count_features(table_list_gdf_nodes2, 'separation_boundary') 

0


In [22]:
count_features(table_list_gdf_nodes2, 'separation_crossing') 

0


In [23]:
count_features(table_list_gdf_nodes2, 'separation_lane') 

0


In [24]:
count_features(table_list_gdf_nodes2, 'separation_line') 

0


In [25]:
count_features(table_list_gdf_nodes2, 'separation_zone') 

6


In [26]:
count_features(table_list_gdf_nodes2, 'cable_submarine')

11


In [190]:
filtered_gdf_seamark(table_list_gdf_nodes2, 'buoy_lateral')

id  version  user_id               tstamp  changeset_id   
51       7795252950        2  2831457  2021-03-23 13:01:51     101576173  \
52       7795252951        1  2831457  2020-08-07 19:36:25      89106995   
53       7795252952        1  2831457  2020-08-07 19:36:25      89106995   
54       7795252953        1  2831457  2020-08-07 19:36:25      89106995   
55       7795252954        2  2831457  2020-09-03 18:02:33      90375725   
...             ...      ...      ...                  ...           ...   
2098665  7792520945        1   601867  2020-08-06 21:04:43      89058527   
2098666  7792520946        1   601867  2020-08-06 21:04:43      89058527   
2098667  7792520947        1   601867  2020-08-06 21:04:43      89058527   
2098674  7793605266        2   495247  2022-06-21 08:45:18     122655020   
2098675  7793605267        2   495247  2022-06-21 08:44:42     122654993   

                                                      tags   
51       {'seamark:name': 'SG 11A', 'seamark:type': 'bu...  \
52       {'seamark:name': 'W 21B 5', 'seamark:type': 'b...   
53       {'seamark:name': 'W 21B 3', 'seamark:type': 'b...   
54       {'seamark:name': 'W 21B 1', 'seamark:type': 'b...   
55       {'seamark:name': 'KZ 6', 'seamark:type': 'buoy...   
...                                                    ...   
2098665  {'seamark:name': 'M-2', 'seamark:type': 'buoy_...   
2098666  {'seamark:name': 'M-1a', 'seamark:type': 'buoy...   
2098667  {'seamark:name': 'M-3', 'seamark:type': 'buoy_...   
2098674  {'seamark:name': 'L16', 'seamark:type': 'buoy_...   
2098675  {'seamark:name': 'L2 / 14', 'seamark:type': 'b...   

                              geom  
51        POINT (5.18059 53.32974)  
52        POINT (5.47956 51.88909)  
53        POINT (5.47789 51.88927)  
54        POINT (5.47564 51.88919)  
55        POINT (5.33584 53.08032)  
...                            ...  
2098665  POINT (14.45223 53.85950)  
2098666  POINT (14.47518 53.85179)  
2098667  POINT (14.42946 53.85937)  
2098674   POINT (8.51517 54.61223)  
2098675   POINT (8.50397 54.60755)  

[56802 rows x 7 columns]

## public.ways

In [4]:
import os
import sqlalchemy as db
import pandas as pd
import geopandas as gpd
from dotenv import load_dotenv

# Load the environment variables from the .env file
load_dotenv("./python_docker/.env")


# Connect to the PostgreSQL database using SQLAlchemy
engine = db.create_engine('postgresql://{user}:{pw}@{host}/{db}'
                           .format(user=os.environ.get("POSTGIS_USER"),
                                   pw=os.environ.get("POSTGIS_PASSWORD"),
                                   host="172.18.0.3",
                                   db=os.environ.get("POSTGIS_DATABASE"),
                                   port='5434'))


connection = engine.connect()


# query = "SELECT * FROM nodes LIMIT 500"
query = "SELECT *, linestring AS geom FROM ways"  #linestring is the column representing the geometry 


# Use geopandas to read the SQL query into a dataframe from postgis
table_list_gdf_ways = gpd.read_postgis(query, engine)

# read timestamp type data as string
table_list_gdf_ways['tstamp']=table_list_gdf_ways['tstamp'].dt.strftime('%Y-%m-%d %H:%M:%S')

table_list_gdf_ways.head(100)

OperationalError: (psycopg2.OperationalError) connection to server at "172.18.0.3", port 5432 failed: Connection timed out
	Is the server running on that host and accepting TCP/IP connections?

(Background on this error at: https://sqlalche.me/e/20/e3q8)

In [ ]:
# Create a copy of the df to test the functions
table_list_gdf_ways2 = table_list_gdf_ways.copy()

In [179]:
table_list_gdf_ways2.head()

id  version  user_id               tstamp  changeset_id   
0  856105545        1  2831457  2020-10-06 19:45:01      92067564  \
1  856105546        1  2831457  2020-10-06 19:45:01      92067564   
2  856105547        1  2831457  2020-10-06 19:45:01      92067564   
3  856105548        1  2831457  2020-10-06 19:45:01      92067564   
4  856105549        1  2831457  2020-10-06 19:45:01      92067564   

                                                tags   
0  {'barrier': 'guard_rail', 'seamark:type': 'sho...  \
1  {'barrier': 'guard_rail', 'seamark:type': 'sho...   
2  {'barrier': 'guard_rail', 'seamark:type': 'sho...   
3  {'barrier': 'guard_rail', 'seamark:type': 'sho...   
4  {'barrier': 'guard_rail', 'mooring': 'waiting'...   

                      nodes   
0  [7982638093, 7982638092]  \
1  [7982638097, 7982638096]   
2  [7982638099, 7982638098]   
3  [7982638101, 7982638100]   
4  [7982638105, 7982638104]   

                                          linestring   
0  0102000020E6100000020000008651B5824BFC15402068...  \
1  0102000020E610000002000000E1ACD227030116409EF0...   
2  0102000020E610000002000000D71C7B51160116404351...   
3  0102000020E6100000020000003007E68D380116405B65...   
4  0102000020E610000002000000E6CFB7054B0516401F40...   

                                              geom  
0  LINESTRING (5.49638 53.04002, 5.49628 53.04001)  
1  LINESTRING (5.50099 53.04240, 5.50101 53.04241)  
2  LINESTRING (5.50106 53.04253, 5.50106 53.04251)  
3  LINESTRING (5.50119 53.04252, 5.50117 53.04251)  
4  LINESTRING (5.50517 53.04859, 5.50540 53.04884)

In [44]:
count_features(table_list_gdf_ways2, 'buoy_lateral') #node - node 

2


In [45]:
count_features(table_list_gdf_ways2, 'separation_bounday')

0


In [46]:
count_features(table_list_gdf_ways2, 'separation_crossing') 

2


In [47]:
count_features(table_list_gdf_ways2, 'separation_lane') 

848


In [48]:
count_features(table_list_gdf_ways2, 'separation_line')

131


In [49]:
count_features(table_list_gdf_ways2, 'separation_zone') 

358


In [50]:
count_features(table_list_gdf_ways2, 'cable_submarine')  

8022


In [193]:
filtered_gdf_seamark(table_list_gdf_ways2, 'separation_zone')

id  version  user_id               tstamp  changeset_id   
69      864611604        2   261189  2020-11-03 11:33:39      93479594  \
89      864611605        2   261189  2020-11-03 15:59:00      93492401   
494     864611602        2   261189  2020-11-03 15:59:00      93492401   
567     864611603        2   261189  2020-11-03 15:59:00      93492401   
1009    866622799        1   261189  2020-11-03 11:33:39      93479594   
...           ...      ...      ...                  ...           ...   
88600   775422874        2    78466  2022-05-07 19:27:11     120680158   
88601   775422875        1    78466  2020-02-21 22:44:06      81334982   
88602   775422876        2   156646  2021-05-21 21:59:28     105113030   
88990   780255530        1  2831457  2020-03-11 17:09:01      82071325   
100533  831291014        1   252955  2020-07-28 15:58:09      88630426   

                                                     tags   
69                    {'seamark:type': 'separation_zone'}  \
89                    {'seamark:type': 'separation_zone'}   
494                   {'seamark:type': 'separation_zone'}   
567                   {'seamark:type': 'separation_zone'}   
1009                  {'seamark:type': 'separation_zone'}   
...                                                   ...   
88600   {'name': 'TSS Entrance to The Sound', 'seamark...   
88601   {'name': 'TSS Entrance to The Sound', 'seamark...   
88602   {'name': 'TSS Entrance to The Sound', 'seamark...   
88990   {'seamark:type': 'separation_zone', 'seamark:s...   
100533                {'seamark:type': 'separation_zone'}   

                                                    nodes   
69      [8077647457, 8077647456, 8077647455, 805883205...  \
89      [8078364279, 8078364277, 8078364278, 805883205...   
494     [8078364275, 8078364276, 8058832046, 807836427...   
567     [8078364271, 8058832048, 8078364273, 807836427...   
1009    [8077647474, 8077647473, 8077647472, 807764747...   
...                                                   ...   
88600   [7234289693, 7234289692, 7234289691, 723428969...   
88601   [7234289985, 7234289885, 7234289785, 723428969...   
88602   [7234289489, 7234289786, 7234289488, 723428969...   
88990   [7285483912, 7285483911, 7285483910, 728548390...   
100533  [7761795140, 7761795145, 7761768177, 776179514...   

                                               linestring   
69      0102000020E61000000700000051DA1B7C61765C40AE30...  \
89      0102000020E610000005000000A6F4A7E823795C4023DB...   
494     0102000020E610000005000000DBF97E6ABC745C40DE71...   
567     0102000020E6100000050000007A200D0206745C40DE7C...   
1009    0102000020E6100000050000005E6166448E8C5C404E4B...   
...                                                   ...   
88600   0102000020E610000007000000B9991B1DA1EC2840F3D1...   
88601   0102000020E6100000050000008CE77D2DF9C5284077BE...   
88602   0102000020E610000005000000EE2C301AE8D428409EEF...   
88990   0102000020E6100000050000003982AF4390CE0C4032CB...   
100533  0102000020E6100000150000006519E25817DB53C00337...   

                                                     geom  
69      LINESTRING (113.84970 22.13898, 113.83678 22.1...  
89      LINESTRING (113.89282 22.14225, 113.84680 22.1...  
494     LINESTRING (113.82400 22.19880, 113.82583 22.1...  
567     LINESTRING (113.81287 22.19083, 113.79857 22.1...  
1009    LINESTRING (114.19618 22.13173, 114.10750 22.1...  
...                                                   ...  
88600   LINESTRING (12.46217 56.18967, 12.46817 56.176...  
88601   LINESTRING (12.38667 56.16550, 12.43517 56.142...  
88602   LINESTRING (12.41583 56.18200, 12.45767 56.155...  
88990   LINESTRING (3.60086 51.43134, 3.57586 51.42981...  
100533  LINESTRING (-79.42330 8.75662, -79.44998 8.744...  

[358 rows x 9 columns]

#### Creating openseamap with filtered tag

In [ ]:
import folium

separation_zones_gdf = filtered_gdf_seamark(table_list_gdf_ways2, 'separation_zone')

# Create a map centered on Germany with a zoom level of 6
map = folium.Map(location=[51.1657, 10.4515], zoom_start=6)

# Add OpenSeaMap tiles as a base layer
folium.TileLayer('http://tiles.openseamap.org/seamark/{z}/{x}/{y}.png',
                 name='OpenSeaMap',
                 attr='Map data © OpenSeaMap contributors').add_to(map)


#Add geodataframe to the map 
folium.GeoJson(separation_zones_gdf,popup=folium.GeoJsonPopup(fields=list(separation_zones_gdf.columns[:-1]))).add_to(map)

               
# Display the map
map

In [216]:
import folium

separation_lines_gdf = filtered_gdf_seamark(table_list_gdf_ways2, 'separation_line')

# Create a map centered on Germany with a zoom level of 6
map = folium.Map(location=[51.1657, 10.4515], zoom_start=6)

# Add OpenSeaMap tiles as a base layer
folium.TileLayer('http://tiles.openseamap.org/seamark/{z}/{x}/{y}.png',
                 name='OpenSeaMap',
                 attr='Map data © OpenSeaMap contributors').add_to(map)


#Add geodataframe to the map 
folium.GeoJson(separation_zones_gdf,popup=folium.GeoJsonPopup(fields=list(separation_zones_gdf.columns[:-1]))).add_to(map)

               
# Display the map
map

In [212]:
def visualize_data_map(gdf, ):

    import folium

    separation_lines_gdf = filtered_gdf_seamark(table_list_gdf_ways2, 'separation_lines')

    # Create a map centered on Germany with a zoom level of 6
    map = folium.Map(location=[51.1657, 10.4515], zoom_start=6)

    # Add OpenSeaMap tiles as a base layer
    folium.TileLayer('http://tiles.openseamap.org/seamark/{z}/{x}/{y}.png',
                     name='OpenSeaMap',
                     attr='Map data © OpenSeaMap contributors').add_to(map)


    #Add geodataframe to the map 
    folium.GeoJson(separation_zones_gdf,popup=folium.GeoJsonPopup(fields=list(separation_zones_gdf.columns[:-1]))).add_to(map)


    # Display the map
    map

#### Visualize geodataframe using the explore method in geopandas

In [211]:
table_list_gdf_ways2.explore()

TypeError: 'NoneType' object is not subscriptable

In [57]:
table_list_gdf_nodes.head()

id  version   user_id               tstamp  changeset_id   
0  7794434396        1  11392834  2020-08-07 12:17:42      89092064  \
1  7794434397        2  11392834  2023-04-02 13:03:10     134413348   
2  7794434398        1  11392834  2020-08-07 12:17:42      89092064   
3  7794434399        1  11392834  2020-08-07 12:17:42      89092064   
4  7794434429        4  11392834  2023-04-02 13:03:10     134413348   

                                                tags   
0                                                 {}  \
1                                                 {}   
2                                                 {}   
3                                                 {}   
4  {'name': 'USCGC Cheyenne', 'image': 'https://w...   

                         geom  
0  POINT (-90.20770 38.58973)  
1  POINT (-90.20780 38.58966)  
2  POINT (-90.20787 38.58970)  
3  POINT (-90.20915 38.58901)  
4  POINT (-90.20920 38.58715)

In [58]:
table_list_gdf_ways.head()

id  version  user_id               tstamp  changeset_id   
0  856105545        1  2831457  2020-10-06 19:45:01      92067564  \
1  856105546        1  2831457  2020-10-06 19:45:01      92067564   
2  856105547        1  2831457  2020-10-06 19:45:01      92067564   
3  856105548        1  2831457  2020-10-06 19:45:01      92067564   
4  856105549        1  2831457  2020-10-06 19:45:01      92067564   

                                                tags   
0  {'barrier': 'guard_rail', 'seamark:type': 'sho...  \
1  {'barrier': 'guard_rail', 'seamark:type': 'sho...   
2  {'barrier': 'guard_rail', 'seamark:type': 'sho...   
3  {'barrier': 'guard_rail', 'seamark:type': 'sho...   
4  {'barrier': 'guard_rail', 'mooring': 'waiting'...   

                      nodes   
0  [7982638093, 7982638092]  \
1  [7982638097, 7982638096]   
2  [7982638099, 7982638098]   
3  [7982638101, 7982638100]   
4  [7982638105, 7982638104]   

                                          linestring   
0  0102000020E6100000020000008651B5824BFC15402068...  \
1  0102000020E610000002000000E1ACD227030116409EF0...   
2  0102000020E610000002000000D71C7B51160116404351...   
3  0102000020E6100000020000003007E68D380116405B65...   
4  0102000020E610000002000000E6CFB7054B0516401F40...   

                                              geom  
0  LINESTRING (5.49638 53.04002, 5.49628 53.04001)  
1  LINESTRING (5.50099 53.04240, 5.50101 53.04241)  
2  LINESTRING (5.50106 53.04253, 5.50106 53.04251)  
3  LINESTRING (5.50119 53.04252, 5.50117 53.04251)  
4  LINESTRING (5.50517 53.04859, 5.50540 53.04884)

#### Creating a function for formatting the tags column

In [ ]:
# Apply the formatting function to the dict column
table_list_gdf_ways2['tags'] = table_list_gdf_ways2['tags'].apply(format_dict)
table_list_gdf_ways

In [73]:
import folium

# Create a map centered on Germany with a zoom level of 6
map = folium.Map(location=[51.1657, 10.4515], zoom_start=6)

# Add OpenSeaMap tiles as a base layer
folium.TileLayer('http://tiles.openseamap.org/seamark/{z}/{x}/{y}.png',
                 name='OpenSeaMap',
                 attr='Map data © OpenSeaMap contributors').add_to(map)


#Add geodataframe to the map 
folium.GeoJson(table_list_gdf_ways[:5000],popup=folium.GeoJsonPopup(fields=list(table_list_gdf_ways.columns[:-1]))).add_to(map)

               
# Display the map
map

#### Download urls of seamarks, coastline,water polygons and land polygons

* Pre-extracted seamarks: 
http://tiles.openseamap.org/seamark/world.osm

* coastlines:
https://osmdata.openstreetmap.de/data/coastlines.html

* water polygons:
https://osmdata.openstreetmap.de/data/water-polygons.html

* land polygons:
https://osmdata.openstreetmap.de/data/land-polygons.html



#### Using bounding box with shapefile

In [ ]:
import geopandas as gpd
from shapely.geometry import box

# define the bounding box coordinates
minx, miny, maxx, maxy = 9.5, 53, 30, 66

# create a shapely geometry object from the bounding box coordinates
bbox = box(minx, miny, maxx, maxy)
epsg_code = '4326'


# read the shapefile and subset it to the bounding box
gdf_land = gpd.read_file('C:/Users/Surendra/Downloads/coastlines-split/lines.shp', bbox=bbox)
gdf_land.head()

In [ ]:
#Visualize coastlines using explore method of geopandas
gdf_land.explore()

#### Overlay coastline data to the existing openseamap

In [ ]:
#add coastline data to the map
folium.GeoJson(gdf_land[:100]).add_to(map)
#folium.GeoJson(gdf_land[:100],popup=folium.GeoJsonPopup(fields=('FID',))).add_to(map)
map

#### Using bounding box while querying from the postgis

In [ ]:
#importing shapely to create bounding box geometry
from shapely.geometry import box

min_lon, min_lat, max_lon, max_lat = 9.5, 53, 30, 66
bbox = box(min_lon, min_lat, max_lon, max_lat)

# convert the bounding box geometry to a WKT string
bbox_wkt = bbox.wkt

# create a SQL query that selects the features within the bounding box
query = "SELECT * FROM nodes WHERE ST_Intersects(geom, ST_GeomFromText('{}', 4326))".format(bbox_wkt)

# read the features within the bounding box from the PostGIS database
df = gpd.read_postgis(query, con=connection, geom_col='geom')
df['tags'][400:500]

In [ ]:
#converting the timestamp datatype to string
df['tstamp']=df['tstamp'].dt.strftime('%Y-%m-%d %H:%M:%S')
df[:100].explore()

In [ ]:
#checking the seamark tags for 1000 elements
for k, v in df['tags'][:1000].items():
    if v == {}:  #checks and  displays non empty dictionaries
        continue
    print(v)

In [61]:
type(table_list_gdf_ways['geom'][0])

shapely.geometry.linestring.LineString

In [ ]:
# query for water polygon table from postgis

query = "SELECT * FROM water_polygons "

# Use pandas to read the SQL query into a dataframe
#table_list_df = pd.read_sql(sql_query, engine)

# Use geopandas to read the SQL query into a dataframe from postgis
water_gdf = gpd.read_postgis(query, engine,geom_col='the_geom')

# read timestamp type data as string
#water_gdf['tstamp']=table_list_gdf['tstamp'].dt.strftime('%Y-%m-%d %H:%M:%S')

water_gdf.head()

In [ ]:
water_gdf.plot()

In [ ]:
bbox=(5.221750,53.250549,6.787199,53.681208)

In [ ]:
# Filter the GeoDataFrame to only include features within the bounding box
water_bbox = water_gdf.cx[bbox[0]:bbox[2], bbox[1]:bbox[3]]

# Visualize the filtered GeoDataFrame
water_bbox.plot()

#water_gdf.explore()

In [ ]:
#sql_query = "SELECT table_name FROM information_schema.tables WHERE table_schema = 'public'"

query = "SELECT * FROM lines "

# Use pandas to read the SQL query into a dataframe
#table_list_df = pd.read_sql(sql_query, engine)

# Use geopandas to read the SQL query into a dataframe from postgis
lines_gdf = gpd.read_postgis(query, engine,geom_col='the_geom')

lines_gdf.head()

In [ ]:
lines_gdf.plot()